In [1]:
import sys
import numpy as np
import pandas as pd
import os 
import gc
from tqdm import tqdm, tqdm_notebook
from sklearn.model_selection import StratifiedKFold, KFold
from sklearn.metrics import f1_score, roc_auc_score
from sklearn.metrics import mean_squared_error as mse
from sklearn.preprocessing import LabelEncoder
import datetime
import time
import lightgbm as lgb
import xgboost as xgb
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.filterwarnings('ignore')

In [2]:
path  = '../Data/Train/'
train_sales  = pd.read_csv(path+'train_sales_data.csv')
train_search = pd.read_csv(path+'train_search_data.csv')
train_user   = pd.read_csv(path+'train_user_reply_data.csv')
evaluation_public = pd.read_csv(path+'evaluation_public.csv')
submit_example    = pd.read_csv(path+'submit_example.csv')
data = pd.concat([train_sales, evaluation_public], ignore_index=True)
data = data.merge(train_search, 'left', on=['province', 'adcode', 'model', 'regYear', 'regMonth'])
data = data.merge(train_user, 'left', on=['model', 'regYear', 'regMonth'])
data['label'] = data['salesVolume']
data['id'] = data['id'].fillna(0).astype(int)
look1 = train_sales.drop_duplicates('model').set_index('model')
data['bodyType'] = data['model'].map(train_sales.drop_duplicates('model').set_index('model')['bodyType'])
for i in ['bodyType', 'model']:
    data[i] = data[i].map(dict(zip(data[i].unique(), range(data[i].nunique()))))
data['mt'] = (data['regYear'] - 2016) * 12 + data['regMonth']
data['model_adcode'] = data['adcode'] + data['model']

In [3]:
def get_stat_feature(df_):   
    df = df_.copy()
    stat_feat = []
    df['model_adcode'] = df['adcode'] + df['model']
    df['model_adcode_mt'] = df['model_adcode'] * 100 + df['mt']
    for col in tqdm(['label','popularity']):
        # shift
        for i in [1,2,3,4,5,6,7,8,9,10,11,12]:
            stat_feat.append('shift_model_adcode_mt_{}_{}'.format(col,i))
            df['model_adcode_mt_{}_{}'.format(col,i)] = df['model_adcode_mt'] + i
            df_last = df[~df[col].isnull()].set_index('model_adcode_mt_{}_{}'.format(col,i))
            df['shift_model_adcode_mt_{}_{}'.format(col,i)] = df['model_adcode_mt'].map(df_last[col])
    return df,stat_feat

def score(data, pred='pred_label', label='label', group='model'):
    data['pred_label'] = data['pred_label'].apply(lambda x: 0 if x < 0 else x).round().astype(int)
    data_agg = data.groupby('model').agg({
        pred:  list,
        label: [list, 'mean']
    }).reset_index()
    data_agg.columns = ['_'.join(col).strip() for col in data_agg.columns]
    nrmse_score = []
    for raw in data_agg[['{0}_list'.format(pred), '{0}_list'.format(label), '{0}_mean'.format(label)]].values:
        nrmse_score.append(
            mse(raw[0], raw[1]) ** 0.5 / raw[2]
        )
    print(1 - np.mean(nrmse_score))
    return 1 - np.mean(nrmse_score)

def get_model_type(train_x,train_y,valid_x,valid_y,m_type='lgb'):   
    if m_type == 'lgb':
        model = lgb.LGBMRegressor(
                                num_leaves=2**5-1, reg_alpha=0.25, reg_lambda=0.25, objective='mse',
                                max_depth=-1, learning_rate=0.05, min_child_samples=5, random_state=2019,
                                n_estimators=2000, subsample=0.9, colsample_bytree=0.7,
                                )
        model.fit(train_x, train_y, 
              eval_set=[(train_x, train_y),(valid_x, valid_y)], 
              categorical_feature=cate_feat, 
              early_stopping_rounds=100, verbose=100)      
    elif m_type == 'xgb':
        model = xgb.XGBRegressor(
                                max_depth=5 , learning_rate=0.05, n_estimators=2000, 
                                objective='reg:gamma', tree_method = 'hist',subsample=0.9, 
                                colsample_bytree=0.7, min_child_samples=5,eval_metric = 'rmse' 
                                )
        model.fit(train_x, train_y, 
              eval_set=[(train_x, train_y),(valid_x, valid_y)], 
              early_stopping_rounds=100, verbose=100)   
    return model

def get_train_model(df_, m, m_type='lgb'):
    df = df_.copy()
    # 数据集划分
    st = 13
    all_idx   = (df['mt'].between(st , m-1))
    train_idx = (df['mt'].between(st , m-5))
    valid_idx = (df['mt'].between(m-4, m-4))
    test_idx  = (df['mt'].between(m  , m  ))
    print('all_idx  :',st ,m-1)
    print('train_idx:',st ,m-5)
    print('valid_idx:',m-4,m-4)
    print('test_idx :',m  ,m  )  
    # 最终确认
    train_x = df[train_idx][features]
    train_y = df[train_idx]['label']
    valid_x = df[valid_idx][features]
    valid_y = df[valid_idx]['label']   
    # get model
    model = get_model_type(train_x,train_y,valid_x,valid_y,m_type)  
    # offline
    df['pred_label'] = model.predict(df[features])
    best_score = score(df[valid_idx]) 
    # online
    if m_type == 'lgb':
        model.n_estimators = model.best_iteration_ + 100
        model.fit(df[all_idx][features], df[all_idx]['label'], categorical_feature=cate_feat)
    elif m_type == 'xgb':
        model.n_estimators = model.best_iteration + 100
        model.fit(df[all_idx][features], df[all_idx]['label'])
    df['forecastVolum'] = model.predict(df[features]) 
    print('valid mean:',df[valid_idx]['pred_label'].mean())
    print('true  mean:',df[valid_idx]['label'].mean())
    print('test  mean:',df[test_idx]['forecastVolum'].mean())
    # 阶段结果
    sub = df[test_idx][['id']]
    sub['forecastVolum'] = df[test_idx]['forecastVolum'].apply(lambda x: 0 if x < 0 else x).round().astype(int)  
    return sub,df[valid_idx]['pred_label']



In [4]:
def trend_factor(data):
    '''计算趋势因子'''
    for col in ['adcode', 'model', 'model_adcode']:
        temp_df = pd.DataFrame(columns=[col, 'factor_{}'.format(col)])
        year_1 = (data['mt'].between(1, 12))
        year_2 = (data['mt'].between(13, 24))
        i = 0
        for df in data[col].unique():
            temp1 = data[(data[col] == df) & (year_1)]
            temp2 = data[(data[col] == df) & (year_2)]
            sum1 = temp1['label'].sum()
            sum2 = temp2['label'].sum()
            factor = sum2 / sum1
            temp_df.loc[i] = {col:df, 'factor_{}'.format(col):factor}
            i = i+1
        data = data.merge(temp_df, how='left', on=[col])
    return data

In [5]:
def average_three(data):
    '''构造该月份对应上一年的该月份，该月份的前一个月和该月份的后一个月的平均值，作为新特征'''
    temp_df = pd.DataFrame(columns=['model_adcode', 'mt', 'aver'])
    j = 0
    for i in tqdm([13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28]):
        for df in data['model_adcode'].unique():
            if (i == 13):
                temp1 = data[(data['model_adcode'] == df) & (data['mt'] == i-12)].reset_index().loc[0]['label']
                temp2 = data[(data['model_adcode'] == df) & (data['mt'] == i-11)].reset_index().loc[0]['label']
                average = (temp1+temp2)/2
                temp_df.loc[j] = {'model_adcode':df, 'mt':i, 'aver':average}
                j = j+1
            elif (i >= 13):
                temp1 = data[(data['model_adcode'] == df) & (data['mt'] == i-12)].reset_index().loc[0]['label']
                temp2 = data[(data['model_adcode'] == df) & (data['mt'] == i-11)].reset_index().loc[0]['label']
                temp3 = data[(data['model_adcode'] == df) & (data['mt'] == i-13)].reset_index().loc[0]['label']
                average = (temp1+temp2+temp3)/3
                temp_df.loc[j] = {'model_adcode':df, 'mt':i, 'aver':average}
                j = j+1
    data = data.merge(temp_df, how='left', on=['model_adcode', 'mt'])
    return data

In [6]:
#与correlation函数配套使用
def combine(data, result, mt):
    origin = data.copy()
    df1 = data.copy()
    df2 = result.copy()
    df1 = df1[(df1['mt'] == mt)]
    df1.drop(['c1', 'c2', 'c3', 'c4', 'c5', 'c6', 'c7', 'c8', 'c9', 'c10', 'c11', 'c12', 'c13', 'c14', 'c15'], axis=1, inplace=True)
    df1 = df1.merge(df2, on=['model', 'adcode', 'mt'])
    origin = origin[~(origin['mt'] == mt)]
    n_data = pd.concat([origin, df1], axis=1)
    print(n_data.head())
    return n_data

In [7]:
#计算每种车型销量相关系数
def correlation(data, start, end, mode=0):
    cor = pd.DataFrame()
    for m in tqdm(data['model'].unique()):
        temp = []
        for i in range(1, 24):
            val1 = data[(data['model'] == m) & (data['mt'] == i)]['popularity'].sum()
            val2 = data[(data['model'] == m) & (data['mt'] == i+1)]['popularity'].sum()
            gap = val2-val1
            temp.append(gap)
        cor[m] = temp
    cor = cor.corr()
    top10 = pd.DataFrame()
    for col in cor.columns:
        temp = cor[col].sort_values(ascending=False)
        index = temp.index.tolist()[1:21]
        top10[col] = index
    '''top10的列分别是model编号，10行代表对应model中的相关系数最高的10种车型'''
    result = pd.DataFrame(columns=['model', 'adcode', 'mt', 'c1', 'c2', 'c3', 'c4', 'c5'])
    for i in top10.columns:
        temp = pd.DataFrame(columns=['model', 'adcode', 'mt', 'c1', 'c2', 'c3', 'c4', 'c5'])
        for k in data['adcode'].unique():
            for j in range(start,end):
                line = {'model':i, 'mt':j, 'adcode':k,
                        'c1':data[(data['model']==top10.iloc[0,i])&(data['adcode']==k)&(data['mt']==j-1)]['popularity'].values[0],
                        'c2':data[(data['model']==top10.iloc[1,i])&(data['adcode']==k)&(data['mt']==j-1)]['popularity'].values[0], 
                        'c3':data[(data['model']==top10.iloc[2,i])&(data['adcode']==k)&(data['mt']==j-1)]['popularity'].values[0],
                        'c4':data[(data['model']==top10.iloc[3,i])&(data['adcode']==k)&(data['mt']==j-1)]['popularity'].values[0],
                        'c5':data[(data['model']==top10.iloc[4,i])&(data['adcode']==k)&(data['mt']==j-1)]['popularity'].values[0]}
                print(line)
                result = result.append(line, ignore_index=True)
    print(result)
    print(data.head())
    if mode == 0:
        data = data.merge(result)
    elif mode == 1:
        data = combine(data, result, start)
    print(data)
    return data

In [8]:
#data_df, stat_feat = get_stat_feature(data)
#correlation(data_df)
#data = correlation(data, 13, 26, 0)
#data.to_csv('../Data/Handle/middle.csv', index=False)

In [9]:
for month in [25,26,27,28]: 
    m_type = 'xgb' 
    
    data_df, stat_feat = get_stat_feature(data)
    data_df = correlation(data_df, 13, month+1)
    
    num_feat = ['regYear'] + stat_feat + ['c1', 'c2', 'c3', 'c4', 'c5']
    cate_feat = ['adcode','bodyType','model','regMonth']
    
    if m_type == 'lgb':
        for i in cate_feat:
            data_df[i] = data_df[i].astype('category')
    elif m_type == 'xgb':
        lbl = LabelEncoder()  
        for i in tqdm(cate_feat):
            data_df[i] = lbl.fit_transform(data_df[i].astype(str))
           
    features = num_feat + cate_feat
    print(len(features), len(set(features)))   
    
    sub,val_pred = get_train_model(data_df, month, m_type)
    #将预测出来的结果再重新加入训练文件，以得到下一个月的结果
    data.loc[(data.regMonth==(month-24))&(data.regYear==2018), 'salesVolume'] = sub['forecastVolum'].values
    data.loc[(data.regMonth==(month-24))&(data.regYear==2018), 'label'      ] = sub['forecastVolum'].values
#ratio = trend_factor(data_df)
#print('ratio is: ' + str(ratio))
sub = data.loc[(data.regMonth>=1)&(data.regYear==2018), ['id','salesVolume']]
print(sub)
sub.columns = ['id','forecastVolum']
#sub['forecastVolum'] = sub['forecastVolum'].apply(lambda x: x * ratio) 
sub[['id','forecastVolum']].round().astype(int).to_csv('../Data/Final/model_2_3_1.csv', index=False)

100%|██████████| 60/60 [00:05<00:00, 10.76it/s]


{'model': 0, 'mt': 13, 'adcode': 310000, 'c1': 705.0, 'c2': 754.0, 'c3': 6172.0, 'c4': 3194.0, 'c5': 1472.0}
{'model': 0, 'mt': 14, 'adcode': 310000, 'c1': 491.0, 'c2': 543.0, 'c3': 5273.0, 'c4': 2271.0, 'c5': 1227.0}
{'model': 0, 'mt': 15, 'adcode': 310000, 'c1': 620.0, 'c2': 681.0, 'c3': 6787.0, 'c4': 3074.0, 'c5': 1716.0}
{'model': 0, 'mt': 16, 'adcode': 310000, 'c1': 368.0, 'c2': 428.0, 'c3': 5157.0, 'c4': 2229.0, 'c5': 1167.0}
{'model': 0, 'mt': 17, 'adcode': 310000, 'c1': 281.0, 'c2': 347.0, 'c3': 4995.0, 'c4': 1561.0, 'c5': 1089.0}
{'model': 0, 'mt': 18, 'adcode': 310000, 'c1': 333.0, 'c2': 343.0, 'c3': 4425.0, 'c4': 1537.0, 'c5': 1080.0}
{'model': 0, 'mt': 19, 'adcode': 310000, 'c1': 296.0, 'c2': 308.0, 'c3': 4264.0, 'c4': 1422.0, 'c5': 1045.0}
{'model': 0, 'mt': 20, 'adcode': 310000, 'c1': 337.0, 'c2': 301.0, 'c3': 4472.0, 'c4': 1459.0, 'c5': 1179.0}
{'model': 0, 'mt': 21, 'adcode': 310000, 'c1': 375.0, 'c2': 287.0, 'c3': 4774.0, 'c4': 1484.0, 'c5': 1293.0}
{'model': 0, 'mt': 

{'model': 0, 'mt': 18, 'adcode': 370000, 'c1': 1693.0, 'c2': 1825.0, 'c3': 11102.0, 'c4': 3923.0, 'c5': 3843.0}
{'model': 0, 'mt': 19, 'adcode': 370000, 'c1': 1657.0, 'c2': 1812.0, 'c3': 11116.0, 'c4': 3875.0, 'c5': 3887.0}
{'model': 0, 'mt': 20, 'adcode': 370000, 'c1': 1766.0, 'c2': 1640.0, 'c3': 11563.0, 'c4': 3396.0, 'c5': 4166.0}
{'model': 0, 'mt': 21, 'adcode': 370000, 'c1': 1674.0, 'c2': 1682.0, 'c3': 11845.0, 'c4': 3482.0, 'c5': 4532.0}
{'model': 0, 'mt': 22, 'adcode': 370000, 'c1': 1826.0, 'c2': 1705.0, 'c3': 11054.0, 'c4': 3376.0, 'c5': 4706.0}
{'model': 0, 'mt': 23, 'adcode': 370000, 'c1': 2041.0, 'c2': 1672.0, 'c3': 10266.0, 'c4': 3279.0, 'c5': 4835.0}
{'model': 0, 'mt': 24, 'adcode': 370000, 'c1': 1599.0, 'c2': 1498.0, 'c3': 9433.0, 'c4': 3628.0, 'c5': 4527.0}
{'model': 0, 'mt': 25, 'adcode': 370000, 'c1': 1758.0, 'c2': 1725.0, 'c3': 9877.0, 'c4': 3533.0, 'c5': 5116.0}
{'model': 0, 'mt': 13, 'adcode': 140000, 'c1': 932.0, 'c2': 973.0, 'c3': 3069.0, 'c4': 1854.0, 'c5': 1606.

{'model': 0, 'mt': 15, 'adcode': 130000, 'c1': 1989.0, 'c2': 1803.0, 'c3': 10390.0, 'c4': 5226.0, 'c5': 3822.0}
{'model': 0, 'mt': 16, 'adcode': 130000, 'c1': 1353.0, 'c2': 1221.0, 'c3': 8644.0, 'c4': 3710.0, 'c5': 2882.0}
{'model': 0, 'mt': 17, 'adcode': 130000, 'c1': 1094.0, 'c2': 1003.0, 'c3': 7906.0, 'c4': 2800.0, 'c5': 2735.0}
{'model': 0, 'mt': 18, 'adcode': 130000, 'c1': 1381.0, 'c2': 1071.0, 'c3': 8375.0, 'c4': 2831.0, 'c5': 2991.0}
{'model': 0, 'mt': 19, 'adcode': 130000, 'c1': 1393.0, 'c2': 1038.0, 'c3': 8621.0, 'c4': 2839.0, 'c5': 3037.0}
{'model': 0, 'mt': 20, 'adcode': 130000, 'c1': 1439.0, 'c2': 908.0, 'c3': 8716.0, 'c4': 2485.0, 'c5': 3167.0}
{'model': 0, 'mt': 21, 'adcode': 130000, 'c1': 1389.0, 'c2': 918.0, 'c3': 8810.0, 'c4': 2544.0, 'c5': 3385.0}
{'model': 0, 'mt': 22, 'adcode': 130000, 'c1': 1301.0, 'c2': 859.0, 'c3': 8001.0, 'c4': 2230.0, 'c5': 3329.0}
{'model': 0, 'mt': 23, 'adcode': 130000, 'c1': 1552.0, 'c2': 871.0, 'c3': 7347.0, 'c4': 2110.0, 'c5': 3512.0}
{'mo

{'model': 0, 'mt': 20, 'adcode': 210000, 'c1': 717.0, 'c2': 715.0, 'c3': 5130.0, 'c4': 1234.0, 'c5': 3794.0}
{'model': 0, 'mt': 21, 'adcode': 210000, 'c1': 712.0, 'c2': 721.0, 'c3': 5261.0, 'c4': 1258.0, 'c5': 3857.0}
{'model': 0, 'mt': 22, 'adcode': 210000, 'c1': 717.0, 'c2': 726.0, 'c3': 4795.0, 'c4': 1145.0, 'c5': 3792.0}
{'model': 0, 'mt': 23, 'adcode': 210000, 'c1': 736.0, 'c2': 660.0, 'c3': 4124.0, 'c4': 1071.0, 'c5': 3795.0}
{'model': 0, 'mt': 24, 'adcode': 210000, 'c1': 686.0, 'c2': 674.0, 'c3': 3868.0, 'c4': 1264.0, 'c5': 3847.0}
{'model': 0, 'mt': 25, 'adcode': 210000, 'c1': 611.0, 'c2': 673.0, 'c3': 3936.0, 'c4': 1256.0, 'c5': 4203.0}
{'model': 0, 'mt': 13, 'adcode': 500000, 'c1': 508.0, 'c2': 706.0, 'c3': 2711.0, 'c4': 1877.0, 'c5': 888.0}
{'model': 0, 'mt': 14, 'adcode': 500000, 'c1': 478.0, 'c2': 634.0, 'c3': 2784.0, 'c4': 1817.0, 'c5': 891.0}
{'model': 0, 'mt': 15, 'adcode': 500000, 'c1': 534.0, 'c2': 735.0, 'c3': 3414.0, 'c4': 2179.0, 'c5': 1185.0}
{'model': 0, 'mt': 16

...

{'model': 59, 'mt': 23, 'adcode': 420000, 'c1': 767.0, 'c2': 927.0, 'c3': 2251.0, 'c4': 6565.0, 'c5': 587.0}
{'model': 59, 'mt': 24, 'adcode': 420000, 'c1': 638.0, 'c2': 694.0, 'c3': 1787.0, 'c4': 10574.0, 'c5': 522.0}
{'model': 59, 'mt': 25, 'adcode': 420000, 'c1': 726.0, 'c2': 676.0, 'c3': 1867.0, 'c4': 22298.0, 'c5': 769.0}
{'model': 59, 'mt': 26, 'adcode': 420000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 27, 'adcode': 420000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 28, 'adcode': 420000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 13, 'adcode': 430000, 'c1': 456.0, 'c2': 592.0, 'c3': 1102.0, 'c4': 1059.0, 'c5': 461.0}
{'model': 59, 'mt': 14, 'adcode': 430000, 'c1': 455.0, 'c2': 710.0, 'c3': 1258.0, 'c4': 1025.0, 'c5': 515.0}
{'model': 59, 'mt': 15, 'adcode': 430000, 'c1': 487.0, 'c2': 795.0, 'c3': 1465.0, 'c4': 1164.0, 'c5': 649.0}
{'model': 59, 'mt': 16, 'adcode': 430000, 'c1': 602.0

{'model': 59, 'mt': 21, 'adcode': 610000, 'c1': 316.0, 'c2': 959.0, 'c3': 2136.0, 'c4': 2368.0, 'c5': 537.0}
{'model': 59, 'mt': 22, 'adcode': 610000, 'c1': 306.0, 'c2': 1089.0, 'c3': 2597.0, 'c4': 2695.0, 'c5': 677.0}
{'model': 59, 'mt': 23, 'adcode': 610000, 'c1': 378.0, 'c2': 1018.0, 'c3': 2908.0, 'c4': 3038.0, 'c5': 629.0}
{'model': 59, 'mt': 24, 'adcode': 610000, 'c1': 291.0, 'c2': 795.0, 'c3': 2736.0, 'c4': 3852.0, 'c5': 560.0}
{'model': 59, 'mt': 25, 'adcode': 610000, 'c1': 310.0, 'c2': 774.0, 'c3': 3184.0, 'c4': 6393.0, 'c5': 919.0}
{'model': 59, 'mt': 26, 'adcode': 610000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 27, 'adcode': 610000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 28, 'adcode': 610000, 'c1': nan, 'c2': nan, 'c3': nan, 'c4': nan, 'c5': nan}
{'model': 59, 'mt': 13, 'adcode': 230000, 'c1': 103.0, 'c2': 924.0, 'c3': 814.0, 'c4': 721.0, 'c5': 191.0}
{'model': 59, 'mt': 14, 'adcode': 230000, 'c1': 96.0, '

100%|██████████| 4/4 [00:00<00:00, 40.02it/s]

       adcode  bodyType  forecastVolum    id  model province  regMonth  \
0      310000         0            NaN     0      0       上海         1   
1      530000         0            NaN     0      0       云南         1   
2      150000         0            NaN     0      0      内蒙古         1   
3      110000         0            NaN     0      0       北京         1   
4      510000         0            NaN     0      0       四川         1   
...       ...       ...            ...   ...    ...      ...       ...   
21115  350000         0            NaN  5364     59       福建         4   
21116  210000         0            NaN  5365     59       辽宁         4   
21117  500000         0            NaN  5366     59       重庆         4   
21118  610000         0            NaN  5367     59       陕西         4   
21119  230000         0            NaN  5368     59      黑龙江         4   

       regYear  salesVolume  popularity  ...  \
0         2017        305.0      1072.0  ...   
1         2017 

[0]	validation_0-rmse:900.64740	validation_1-rmse:1451.30005
Multiple eval metrics have been passed: 'validation_1-rmse' will be used for early stopping.

Will train until validation_1-rmse hasn't improved in 100 rounds.
[100]	validation_0-rmse:859.31451	validation_1-rmse:1408.53528
[200]	validation_0-rmse:277.51797	validation_1-rmse:784.37353
[300]	validation_0-rmse:133.80635	validation_1-rmse:724.53748
Stopping. Best iteration:
[232]	validation_0-rmse:167.11679	validation_1-rmse:719.61414

0.4263468954173075
valid mean: 499.5292
true  mean: 899.8204545454546
test  mean: 336.50644
         id  salesVolume
31680     1        245.0
31681     2        317.0
31682     3        153.0
31683     4        223.0
31684     5        399.0
...     ...          ...
36955  5364         48.0
36956  5365         47.0
36957  5366         55.0
36958  5367        104.0
36959  5368         41.0

[5280 rows x 2 columns]
